In [1]:
library(igraph)
library(neat)
library(utils)
library(reshape2)
library(stringr)


Attaching package: ‘igraph’

The following objects are masked from ‘package:stats’:

    decompose, spectrum

The following object is masked from ‘package:base’:

    union



In [2]:
load("../analysis/GENIE.top10.igraph.RData")

In [3]:
n=read.delim("../analysis/GENIE3.top10_target_ranks.communities_PLM.with_node_centralities.csv",sep=";",stringsAsFactors=FALSE)
head(n)

geneid            community degree_centrality betweenness_centrality
1 Pp3c27_3080.mRNA  I         109                  0                  
2 Pp3c11_23290.mRNA I         552               3190                  
3 Pp3c7_2300.mRNA   I         505               7529                  
4 Pp3c17_23620.mRNA I         490               1988                  
5 Pp3c16_13280.mRNA I         485               9982                  
6 Pp3c15_11610.mRNA I         461               3734                  
  eigenvector_centrality local_reaching_centrality centrality_rank
1 0.00000000             0.9977499                 1              
2 0.05359921             0.9971070                 2              
3 0.02518149             0.9971070                 3              
4 0.05419710             0.9971070                 4              
5 0.05634423             0.9971070                 5              
6 0.04049888             0.9971070                 6

In [4]:
com=sapply(as.character(as.roman(1:11)),function(i) n[n$community==i, "geneid"])
str(com)

List of 11
 $ I   : chr [1:3112] "Pp3c27_3080.mRNA" "Pp3c11_23290.mRNA" "Pp3c7_2300.mRNA" "Pp3c17_23620.mRNA" ...
 $ II  : chr [1:4418] "Pp3c15_24790.mRNA" "Pp3c4_14601.pre_miRNA" "Pp3c22_13060.mRNA" "Pp3c9_13190.mRNA" ...
 $ III : chr [1:1705] "Pp3c13_10800.mRNA" "Pp3c22_11080.mRNA" "Pp3c16_9970.mRNA" "Pp3c8_250.mRNA" ...
 $ IV  : chr [1:2728] "Pp3c19_7560.mRNA" "Pp3c19_9880.mRNA" "Pp3c20_7710.mRNA" "Pp3c6_29020.mRNA" ...
 $ V   : chr [1:3435] "Pp3c22_2330.mRNA" "Pp3c5_12740.mRNA" "Pp3c8_6890.mRNA" "Pp3c7_25430.mRNA" ...
 $ VI  : chr [1:1849] "Pp3c16_20970.mRNA" "Pp3c1_32480.mRNA" "Pp3c10_13060.mRNA" "Pp3c4_25130.mRNA" ...
 $ VII : chr [1:3851] "Pp3c2_35433.mRNA" "Pp3c7_24670.mRNA" "Pp3c15_14600.mRNA" "Pp3c9_14240.mRNA" ...
 $ VIII: chr [1:3662] "Pp3c10_2910.mRNA" "Pp3c1_4600.mRNA" "Pp3c14_4440.mRNA" "Pp3c2_15500.mRNA" ...
 $ IX  : chr [1:6167] "Pp3c13_8290.mRNA" "Pp3c5_21130.mRNA" "Pp3c3_31770.mRNA" "Pp3c3_17380.mRNA" ...
 $ X   : chr [1:2403] "Pp3c1_15290.mRNA" "Pp3c16_15450.mRNA" "

In [5]:
e=read.delim("../ontology_enrichment/analysis/significantly_enriched_terms.Benjamini-Hochberg.txt",sep="\t",stringsAsFactors=FALSE)
e=subset(e,depth>1)
head(e)

group    set            method             cutoff ontology ID        
1 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0003700
2 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0003735
4 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0005773
5 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0005840
6 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0005886
7 profiles downDEK1_upOEX Benjamini-Hochberg 0.1    GO       GO:0006412
  Pop.total Pop.term Study.total Study.term ⋯ is.trivial p           
1 4801       266     2544        156        ⋯ false      3.122253e-04
2 4801       248     2544        185        ⋯ false      1.397283e-06
4 4801       738     2544        444        ⋯ false      3.436430e-05
5 4801       284     2544        198        ⋯ false      2.537576e-08
6 4801      1171     2544        683        ⋯ false      8.935718e-05
7 4801       374     2544        231        ⋯ false      8.625273e-05
  p.adjusted   p.min         depth ic        partition         
1 5.421272e-02 4.017094e-155 43     7.674639 molecular_function
2 7.278450e-04  8.039627e-98 16    10.765681 molecular_function
4 1.376951e-02  0.000000e+00 11     6.056151 cellular_component
5 1.550577e-05  0.000000e+00 13     7.721159 cellular_component
6 2.571085e-02  0.000000e+00  5     4.474112 cellular_component
7 2.571085e-02  0.000000e+00 24     5.068588 biological_process
  level3                              name                                     
1 biological_process                  DNA-binding transcription factor activity
2 cellular_component                  structural constituent of ribosome       
4 membrane-bounded organelle          vacuole                                  
5 non-membrane-bounded organelle      ribosome                                 
6 cell                                plasma membrane                          
7 organic substance metabolic process translation                              
  loci                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [6]:
cutoff =0.1
k=as.data.frame(table(e$group,e$set,e$ID))
k=k[k$Freq>0,]
row.names(k)=paste(k[,1],k[,2],k[,3],sep=":")
nrow(k)
k


[1] 10134

Var1                   
subnetworks:IX:GO:0000028                     subnetworks            
subnetwork_regulation:IX_neg:GO:0000028       subnetwork_regulation  
subnetwork_regulation:VII_pos:GO:0000035      subnetwork_regulation  
subnetworks:IX:GO:0000036                     subnetworks            
subnetworks:X:GO:0000038                      subnetworks            
subnetwork_regulation:X_pos:GO:0000038        subnetwork_regulation  
subnetwork_regulation:I_pos:GO:0000041        subnetwork_regulation  
subnetworks:VIII:GO:0000049                   subnetworks            
subnetwork_regulation:VIII_pos:GO:0000049     subnetwork_regulation  
subnetwork_regulation:IX_pos:GO:0000075       subnetwork_regulation  
subnetwork_deregulation:V:GO:0000075          subnetwork_deregulation
subnetworks:V:GO:0000075                      subnetworks            
subnetwork_regulation:V_pos:GO:0000075        subnetwork_regulation  
subnetworks:IX:GO:0000077                     subnetworks            
subnetwork_profiles:profile1_in_V:GO:0000087  subnetwork_profiles    
subnetwork_deregulation:V:GO:0000087          subnetwork_deregulation
subnetwork_regulation:VIII_pos:GO:0000095     subnetwork_regulation  
subnetworks:VIII:GO:0000096                   subnetworks            
subnetwork_regulation:VIII_pos:GO:0000096     subnetwork_regulation  
subnetwork_regulation:V_pos:GO:0000105        subnetwork_regulation  
subnetwork_regulation:VII_pos:GO:0000118      subnetwork_regulation  
subnetworks:VII:GO:0000122                    subnetworks            
subnetwork_regulation:VII_pos:GO:0000122      subnetwork_regulation  
subnetworks:V:GO:0000139                      subnetworks            
subnetwork_regulation:V_pos:GO:0000139        subnetwork_regulation  
subnetworks:V:GO:0000148                      subnetworks            
subnetwork_regulation:V_pos:GO:0000148        subnetwork_regulation  
subnetwork_regulation:I_pos:GO:0000149        subnetwork_regulation  
subnetworks:IX:GO:0000151                     subnetworks            
subnetwork_regulation:IX_pos:GO:0000151       subnetwork_regulation  
⋮                                             ⋮                      
subnetwork_deregulation:VIII:PO:0030086       subnetwork_deregulation
subnetworks:VIII:PO:0030086                   subnetworks            
subnetwork_regulation:VIII_pos:PO:0030086     subnetwork_regulation  
subnetwork_deregulation:X:PO:0030086          subnetwork_deregulation
subnetworks:XI:PO:0030086                     subnetworks            
subnetwork_regulation:XI_pos:PO:0030086       subnetwork_regulation  
subnetwork_deregulation:IX:PO:0030112         subnetwork_deregulation
subnetworks:IX:PO:0030112                     subnetworks            
subnetwork_regulation:IX_neg:PO:0030112       subnetwork_regulation  
subnetwork_regulation:IX_pos:PO:0030112       subnetwork_regulation  
subnetwork_profiles:profile1_in_IX:PO:0030112 subnetwork_profiles    
subnetwork_profiles:profile2_in_IX:PO:0030112 subnetwork_profiles    
subnetwork_deregulation:V:PO:0030112          subnetwork_deregulation
subnetwork_regulation:V_pos:PO:0030112        subnetwork_regulation  
subnetwork_deregulation:VII:PO:0030112        subnetwork_deregulation
subnetworks:VII:PO:0030112                    subnetworks            
subnetwork_regulation:VII_pos:PO:0030112      subnetwork_regulation  
subnetworks:VIII:PO:0030112                   subnetworks            
subnetwork_regulation:VIII_pos:PO:0030112     subnetwork_regulation  
subnetworks:III:PO:0030114                    subnetworks            
subnetwork_profiles:profile2_in_X:PO:0030114  subnetwork_profiles    
subnetwork_deregulation:X:PO:0030114          subnetwork_deregulation
subnetworks:X:PO:0030114                      subnetworks            
subnetwork_regulation:X_pos:PO:0030114        subnetwork_regulation  
subnetworks:X:TO:0000283                      subnetworks            
subnetwork_regulation:X_pos:TO:0000283        subnetwork

In [7]:
k$community=ifelse(k$Var1=="subnetworks" | k$Var1=="subnetwork_deregulation",as.character(k$Var2),
             ifelse(k$Var1=="subnetwork_profiles",str_match(k$Var2,"profile\\d+_in_(.+)")[,2],
                    ifelse(k$Var1=="subnetwork_regulation",str_match(k$Var2,"^([^_]+)_")[,2],NA)))

In [8]:
L=sapply(row.names(k),function(i) {
    K=t(k[i,])
    unique(strsplit(subset(e,group==K[1] & set==K[2] & ID==K[3])$loci,","))
})
str(L)

List of 10134
 $ subnetworks:IX:GO:0000028                      : chr [1:28] "Pp3c4_6610.mRNA" "Pp3c23_6150.mRNA" "Pp3c24_18880.mRNA" "Pp3c14_15700.mRNA" ...
 $ subnetwork_regulation:IX_neg:GO:0000028        : chr [1:10] "Pp3c8_16820.mRNA" "Pp3c17_17600.mRNA" "Pp3c23_6150.mRNA" "Pp3c8_16860.mRNA" ...
 $ subnetwork_regulation:VII_pos:GO:0000035       : chr [1:2] "Pp3c12_14430.mRNA" "Pp3c4_7570.mRNA"
 $ subnetworks:IX:GO:0000036                      : chr [1:7] "Pp3c20_7570.mRNA" "Pp3c13_14790.mRNA" "Pp3c10_8470.mRNA" "Pp3c14_24710.mRNA" ...
 $ subnetworks:X:GO:0000038                       : chr [1:8] "Pp3c9_4680.mRNA" "Pp3c24_290.mRNA" "Pp3c17_2780.mRNA" "Pp3c9_22960.mRNA" ...
 $ subnetwork_regulation:X_pos:GO:0000038         : chr [1:8] "Pp3c9_4680.mRNA" "Pp3c24_290.mRNA" "Pp3c17_2780.mRNA" "Pp3c9_22960.mRNA" ...
 $ subnetwork_regulation:I_pos:GO:0000041         : chr [1:31] "Pp3c1_2880.mRNA" "Pp3c20_13520.mRNA" "Pp3c7_12200.mRNA" "Pp3c2_16170.mRNA" ...
 $ subnetworks:VIII:GO:0000049 

In [10]:
test = neat(blist = L, alist = com, network = G, nettype = 'directed', nodes = n$geneid, alpha = 0.05) 

In [11]:
nrow(test)
head(test)

[1] 111474

A B                                        nab expected_nab pvalue      
1 I subnetworks:IX:GO:0000028                6   25.3256      2.764519e-06
2 I subnetwork_regulation:IX_neg:GO:0000028  0    9.0448      7.623067e-05
3 I subnetwork_regulation:VII_pos:GO:0000035 2    1.8090      8.202782e-01
4 I subnetworks:IX:GO:0000036                3    6.3314      1.541349e-01
5 I subnetworks:X:GO:0000038                 0    7.2359      5.079263e-04
6 I subnetwork_regulation:X_pos:GO:0000038   0    7.2359      5.079263e-04
  conclusion     
1 Underenrichment
2 Underenrichment
3 No enrichment  
4 No enrichment  
5 Underenrichment
6 Underenrichment

In [9]:
table(k$Var1)


               profiles subnetwork_deregulation     subnetwork_profiles 
                    171                    1152                    1059 
  subnetwork_regulation             subnetworks 
                   4016                    3736 

In [12]:
subsets=read.delim("PO.subsets.tsv",sep="\t",header=FALSE,stringsAsFactors=FALSE)
names(subsets)=c("ID","subset")
head(subsets)
table(subsets$subset)

ID         subset    
1 PO:0000002 Angiosperm
2 PO:0000002 reference 
3 PO:0000003 reference 
4 PO:0000003 TraitNet  
5 PO:0000005 CL        
6 PO:0000006 CL


   Angiosperm   Arabidopsis    Bryophytes        Citrus            CL 
           73            31            89            20           161 
  Gymnosperms         Maize          Musa       Poaceae        Potato 
           20           102            29            46            21 
Pteridophytes     reference          Rice        Tomato      TraitNet 
           37           133            35            23           172 

In [13]:
Test=merge(k,subset(test,conclusion=="Overenrichment"),by.x=0,by.y=2)
Test=subset(Test,community==as.character(A))
Test$fdr=p.adjust(Test$pvalue,method="fdr")
Test$bonferroni=p.adjust(Test$pvalue,method="bonferroni")
Test=merge(e[e$p.adjusted<0.01,c(1,2,5:13,15:22)],subset(Test,fdr<0.01 ),by.x=c(1,2,4),by.y=2:4)
nrow(Test)
head(Test)

[1] 5615

group                   set ID         ontology Pop.total Pop.term
1 subnetwork_deregulation I   GO:0044425 GO       27502      4562   
2 subnetwork_deregulation I   PO:0000004 PO       21797     14965   
3 subnetwork_deregulation I   PO:0000005 PO       21797     14965   
4 subnetwork_deregulation I   PO:0007045 PO       21797      8227   
5 subnetwork_deregulation I   PO:0007057 PO       21797      8492   
6 subnetwork_deregulation I   PO:0007130 PO       21797     10148   
  Study.total Study.term Pop.family Study.family ⋯
1 317          92        24699      291          ⋯
2 312         262        21797      312          ⋯
3 312         262        21358      311          ⋯
4 312         141        11925      174          ⋯
5 312         146        11925      174          ⋯
6 312         161        12695      179          ⋯
  Row.names                            Freq community A nab  expected_nab
1 subnetwork_deregulation:I:GO:0044425 1    I         I  551  83.2126    
2 subnetwork_deregulation:I:PO:0000004 1    I         I 1537 236.9751    
3 subnetwork_deregulation:I:PO:0000005 1    I         I 1537 236.9751    
4 subnetwork_deregulation:I:PO:0007045 1    I         I  792 127.5324    
5 subnetwork_deregulation:I:PO:0007057 1    I         I  825 132.0548    
6 subnetwork_deregulation:I:PO:0007130 1    I         I  903 145.6221    
  pvalue conclusion     fdr bonferroni
1 0      Overenrichment 0   0         
2 0      Overenrichment 0   0         
3 0      Overenrichment 0   0         
4 0      Overenrichment 0   0         
5 0      Overenrichment 0   0         
6 0      Overenrichment 0   0

In [14]:
table(Test$group,Test$set,Test$partition)

, ,  = biological_process

                         
                            I I_neg I_pos  II II_pos III III_pos  IV IV_pos  IX
  subnetwork_deregulation   0     0     0   7      0   0       0   0      0  59
  subnetwork_profiles       0     0     0   0      0   0       0   0      0   0
  subnetwork_regulation     0     0   120   0     31   0      52   0     13   0
  subnetworks              75     0     0  44      0  71       0  24      0 202
                         
                          IX_neg IX_pos profile1_in_I profile1_in_II
  subnetwork_deregulation      0      0             0              0
  subnetwork_profiles          0      0             1              4
  subnetwork_regulation       61    179             0              0
  subnetworks                  0      0             0              0
                         
                          profile1_in_IX profile1_in_V profile1_in_VII
  subnetwork_deregulation              0             0               0
  subnet

In [16]:
QQ=subset(Test,partition=="plant anatomical entity" & group =="subnetwork_deregulation")
table(QQ$name,QQ$set)

                                               
                                                I III IX V VII VIII X
  androecium                                    0   0  1 0   0    0 0
  androecium primordium                         0   0  1 0   0    0 0
  anther                                        0   0  1 0   0    1 0
  bract                                         0   0  1 0   1    0 0
  bract anlagen                                 0   0  1 0   1    0 0
  bract primordium                              0   0  1 0   1    0 0
  branch                                        0   0  1 0   1    0 0
  bud                                           0   0  0 0   0    1 1
  cardinal organ part                           0   0  1 0   0    1 0
  cardinal part of multi-tissue plant structure 0   0  1 0   0    1 0
  carpel                                        0   0  1 0   0    0 0
  carpel anlagen                                0   0  1 1   1    0 0
  carpel primordium                       

In [17]:
QQ=subset(Test,partition=="plant anatomical entity" & group =="subnetworks")
table(QQ$name,QQ$set)

                                               
                                                I III IX V VII VIII X XI
  abscission zone                               1   0  0 0   0    0 0  0
  adult vascular leaf                           1   0  0 0   0    0 0  0
  androecium                                    0   0  1 0   0    1 0  0
  androecium primordium                         0   0  1 0   0    1 0  0
  anther                                        0   0  1 0   0    1 0  0
  anther wall                                   0   1  0 0   0    0 0  0
  apical meristem                               1   0  1 0   0    1 0  1
  axillary vegetative bud                       0   0  0 0   1    0 0  0
  bract                                         0   0  1 0   1    1 0  0
  bract anlagen                                 0   0  1 0   1    1 0  0
  bract primordium                              0   0  1 0   1    1 0  0
  branch                                        0   0  1 0   1    1 0  0
  b

In [18]:
QQ=subset(Test,partition=="plant anatomical entity" & ID %in% subset(subsets,subset=="Bryophytes")$ID)
table(QQ$name,QQ$set)

                                   
                                    I I_pos II_pos III III_pos IX IX_neg IX_pos
  gametophore                       0     0      0   0       0  2      1      0
  gametophore bud                   0     0      0   0       0  2      1      0
  non-vascular leaf                 1     1      0   0       0  0      0      0
  protonema                         0     0      0   0       0  2      1      0
  protonema sub-apical initial cell 0     0      1   0       0  0      1      0
  sporangium                        0     0      0   2       1  1      0      1
                                   
                                    profile1_in_V profile2_in_III
  gametophore                                   0               0
  gametophore bud                               0               0
  non-vascular leaf                             0               0
  protonema                                     1               0
  protonema sub-apical initial cell   

In [19]:
QQ=subset(Test,partition=="plant structure development stage" & group =="subnetwork_deregulation")
table(QQ$name,QQ$set)

                                                      
                                                       I II III IX V VII VIII X
  1 main shoot growth stage                            0  0   0  1 1   0    0 0
  bud development stage                                0  0   0  0 0   0    1 1
  coleoptile emergence stage                           1  0   0  1 0   0    0 0
  collective phyllome structure development stage      0  0   0  1 0   0    1 0
  collective plant organ structure development stage   0  0   0  1 0   0    1 0
  flower development stage                             0  0   0  1 0   0    0 0
  gametophore vegetative whole plant development stage 0  0   0  0 0   0    1 1
  gametophyte development stage                        0  0   0  0 1   0    0 0
  gametophyte vegetative stage                         0  1   0  0 1   0    1 1
  IL.00 inflorescence just visible stage               0  0   0  1 0   0    0 0
  L mature pollen stage                                0  0   0  

In [20]:
QQ=subset(Test,partition=="plant structure development stage" & group =="subnetworks")
table(QQ$name,QQ$set)

                                                      
                                                       I II III IX V VII VIII X
  1 main shoot growth stage                            0  0   0  1 0   1    1 0
  androecium development stage                         1  0   0  0 0   1    0 0
  bud development stage                                0  0   0  0 0   0    1 0
  calyx development stage                              0  0   0  0 0   1    0 0
  coleoptile emergence stage                           0  0   0  1 0   1    0 0
  collective phyllome structure development stage      0  0   0  1 0   0    1 0
  collective plant organ structure development stage   0  0   0  1 0   0    1 0
  corolla development stage                            0  0   0  0 0   0    1 0
  D pollen mother cell meiosis stage                   0  0   0  1 0   0    0 0
  developing seed stage                                0  0   0  0 0   0    0 0
  dry seed stage                                       0  0   0  

In [23]:
QQ=subset(Test,partition=="biological_process" & ic <4 &  group =="subnetwork_deregulation" & round(Study.term/Study.total,2)>=0.1)
table(QQ$name,QQ$set)

                                                  
                                                   II IX V VII VIII X
  anatomical structure development                  0  1 0   1    0 0
  cell communication                                0  0 0   0    0 1
  cellular macromolecule biosynthetic process       0  1 0   0    0 0
  cellular macromolecule metabolic process          0  1 0   0    0 0
  cellular metabolic process                        0  1 0   0    0 0
  cellular nitrogen compound metabolic process      0  1 0   0    0 0
  cellular protein metabolic process                0  1 0   0    0 0
  gene expression                                   0  1 0   0    0 0
  macromolecule biosynthetic process                0  1 0   0    0 0
  macromolecule metabolic process                   0  1 0   0    0 0
  nitrogen compound metabolic process               0  1 0   0    0 0
  nucleic acid metabolic process                    0  1 0   0    0 0
  nucleobase-containing compound metabo

In [24]:
QQ=subset(Test,partition=="biological_process" & ic <4 &  group =="subnetworks" & round(Study.term/Study.total,2)>=0.1)
table(QQ$name,QQ$set)

                                                     
                                                      I II III IV IX V VI VII
  anatomical structure development                    0  0   0  0  1 0  0   1
  aromatic compound biosynthetic process              0  1   0  1  0 0  0   0
  biosynthetic process                                0  0   0  0  1 0  0   0
  cell communication                                  1  1   0  0  0 0  0   0
  cellular aromatic compound metabolic process        0  0   0  1  1 0  0   0
  cellular biosynthetic process                       0  0   0  0  1 0  0   0
  cellular component assembly                         0  0   0  0  0 0  0   0
  cellular component biogenesis                       0  0   0  0  0 0  0   0
  cellular component organization                     0  0   0  0  0 1  0   0
  cellular macromolecule biosynthetic process         0  0   0  0  1 0  0   0
  cellular macromolecule metabolic process            0  0   0  1  1 0  0   1
  cellular

In [25]:
Test=merge(k,subset(test,conclusion=="Overenrichment"),by.x=0,by.y=2)
Test=subset(Test,community==as.character(A))
Test$fdr=p.adjust(Test$pvalue,method="fdr")
Test$bonferroni=p.adjust(Test$pvalue,method="bonferroni")
Test=merge(e,Test[,-c(1,5)],by.x=c(1,2,6),by.y=1:3)
nrow(Test)
Test=Test[,c(1:22,24:31,23)]
head(Test)

[1] 9906

group                   set ID         method             cutoff ontology
1 subnetwork_deregulation I   GO:0005773 Benjamini-Hochberg 0.1    GO      
2 subnetwork_deregulation I   GO:0005794 Benjamini-Hochberg 0.1    GO      
3 subnetwork_deregulation I   GO:0005886 Benjamini-Hochberg 0.1    GO      
4 subnetwork_deregulation I   GO:0006629 Benjamini-Hochberg 0.1    GO      
5 subnetwork_deregulation I   GO:0006970 Benjamini-Hochberg 0.1    GO      
6 subnetwork_deregulation I   GO:0007530 Benjamini-Hochberg 0.1    GO      
  Pop.total Pop.term Study.total Study.term ⋯ name                      
1 27502     3332     317          62        ⋯ vacuole                   
2 27502     1412     317          33        ⋯ Golgi apparatus           
3 27502     5743     317          97        ⋯ plasma membrane           
4 27502     1106     317          30        ⋯ lipid metabolic process   
5 27502     5007     317         106        ⋯ response to osmotic stress
6 27502        9     317           3        ⋯ sex determination         
  community A nab expected_nab pvalue        conclusion     fdr          
1 I         I 364 56.0781      1.265726e-211 Overenrichment 2.177919e-211
2 I         I 194 29.8480      4.761608e-114 Overenrichment 6.857879e-114
3 I         I 557 87.7350      1.044596e-315 Overenrichment 2.073701e-315
4 I         I 169 26.2301       8.349873e-99 Overenrichment  1.158619e-98
5 I         I 667 94.0664       0.000000e+00 Overenrichment  0.000000e+00
6 I         I  15  2.7135       9.959996e-09 Overenrichment  1.008935e-08
  bonferroni   
1 1.253828e-207
2 4.716849e-110
3 1.034777e-311
4  8.271384e-95
5  0.000000e+00
6  9.866372e-05
  loci                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
1 Pp3c2_2860.mRNA,Pp3c4_27720.mRNA,Pp3c26_15370.mRNA,Pp3c20_5190.mRNA,Pp3c6_3120.mRNA,Pp3c10_9960.mRNA,Pp3c16_2360.mRNA,Pp3c7_5350.mRNA,Pp3c21_9640.mRNA,Pp3c14_13380.mRNA,Pp3c10_6970.mRNA,Pp3c19_20830.mRNA,Pp3c2_10280.mRNA,Pp3c10_2340.mRNA,Pp3c1_24840.mRNA,Pp3c10_2650.mRNA,Pp3c11_24160.mRNA,Pp3c3_5770.mRNA,Pp3c20_9730.mRNA,Pp3c23_13640.mRNA,Pp3c8_15380.mRNA,Pp3c15_4030.mRNA,Pp3c22_20020.mRNA,Pp3c4_27680.mRNA,Pp3c14_19880.mRNA,Pp3c3_18340.mRNA,Pp3c4_2110.mRNA,Pp3c8_13050.mRNA,Pp3c22_240.mRNA,Pp3c9_20840.mRNA,Pp3c5_5440.mRNA,Pp3c21_9340.mRNA,Pp3

In [26]:
table(Test$group,Test$partition)

                         
                          biological_process cellular_component
  subnetwork_deregulation                453                129
  subnetwork_profiles                    604                128
  subnetwork_regulation                 2218                381
  subnetworks                           2167                387
                         
                          molecular_function plant anatomical entity
  subnetwork_deregulation                 73                     361
  subnetwork_profiles                     78                     191
  subnetwork_regulation                  459                     737
  subnetworks                            457                     548
                         
                          plant structure development stage
  subnetwork_deregulation                                89
  subnetwork_profiles                                    57
  subnetwork_regulation                                 216
  subnetworks    

In [27]:
write.table(Test,"analysis/significantly_enriched_terms.Benjamini-Hochberg.subnetwork_sets_NEAT.tsv",col.names=TRUE,sep="\t",quote=FALSE,row.names=FALSE)